In [1]:
%load_ext autoreload
%autoreload 2
import numpy as np
import matplotlib.pyplot as plt
import librosa.display
import IPython.display as ipd
from risset import *

In [2]:
def get_note_freq(p):
    """
    Return the frequency corresponding to a particular
    note number
    Parameters
    ----------
    p: int
        Note number, in halfsteps.  0 is a concert a
    """
    return 440*2**(p/12)

def load_tune(filename, tune_length):
    """
    Load in information about notes and their
    onset times from a text file
    Parameters
    ----------
    filename: string
        Path to file with the tune
    tune_length: float
        Length, in seconds, of the tune
    
    Returns
    -------
    ps: ndarray(N)
        A list of N note numbers
    times: ndarray(N)
        Duration of each note, in increments
        of sixteenth notes
    """
    tune = np.loadtxt(filename)
    ps = tune[:, 0]
    times = np.zeros(tune.shape[0])
    times[1::] = np.cumsum(tune[0:-1, 1])
    times = times*tune_length/np.sum(tune[:, 1])
    times = times[np.isnan(ps)==0]
    ps = ps[np.isnan(ps)==0]
    return ps, times

# Slow Risset

In [3]:
def do_risset_slow(filename, tune_length, freqs_per_note, sr):
    """
    Implement the naive version of Risset beats where 
    freqs_per_note sinusoids are added for every note
    Parameters
    ----------
    filename: string
        Path to file with the tune
    tune_length: float
        Length, in seconds, of the tune
    freqs_per_note: int
        Number of frequencies to use for each note
    sr: int
        The sample rate of the entire piece
    """
    ps, times = load_tune(filename, tune_length)
    ts = np.arange(int(tune_length*sr))/sr
    y = np.zeros_like(ts)
    ## TODO: Fill this in
    for p, time in zip(ps, times):
        freq = get_note_freq(p)
        diff = (1/tune_length)*freqs_per_note
        
        #fs = np.linspace(freq-diff, freq+diff, num=freqs_per_note)
        freqs = np.arange(freq-diff/2, freq+diff/2, 1/tune_length)

        for f in freqs:
            u = ts - time
            y += np.sin(2*np.pi*f*u) + np.cos(2*np.pi*f*u)
   
    return y

# Fast Risset

In [24]:
def do_risset_fast(filename, tune_length, freqs_per_note, sr):
    """
    Implement the faster version of Risset beats that aggregates
    duplicate frequencies into a sine and cosine term
    Parameters
    ----------
    filename: string
        Path to file with the tune
    tune_length: float
        Length, in seconds, of the tune
    freqs_per_note: int
        Number of frequencies to use for each note
    sr: int
        The sample rate of the entire piece
    """
    ps, times = load_tune(filename, tune_length)
    ts = np.arange(int(tune_length*sr))/sr
    y = np.zeros_like(ts)
    ## TODO: Fill this in
    sin_amps = {}
    cos_amps = {}
    for p, time in zip(ps, times):
        freq = get_note_freq(p)
        diff = (1/tune_length)*freqs_per_note
        freqs = np.arange(freq-diff/2, freq+diff/2, 1/tune_length)
        for f in freqs:
            if f not in sin_amps:
                sin_amps[f] = np.sin(2*np.pi*f*time)
                cos_amps[f] = np.cos(2*np.pi*f*time)
            
            sin_amps[f] += np.sin(2*np.pi*f*time)
            cos_amps[f] += np.cos(2*np.pi*f*time)
    
    for f in sin_amps:
        sinAmp = sin_amps[f]
        cosAmp = cos_amps[f]
        y += sinAmp*np.sin(2*np.pi*f*ts) + cosAmp*np.cos(2*np.pi*f*ts)
    return y

# Musical Statement

In [11]:
import time

In [30]:
# sample rate = 44100 not 8000
# for musical statement
tune_length = 10
freqs_per_note = 100
sr = 44100
tic = time.perf_counter()
x = do_risset_slow("Tunes/Henry_music_work.txt", tune_length, freqs_per_note, sr)
toc = time.perf_counter()
print(f"Slow risset took {toc - tic:0.4f} seconds")
ipd.Audio(x, rate=sr)

Slow risset took 6.3127 seconds


In [31]:
tune_length = 10
freqs_per_note = 100
sr = 44100
tic = time.perf_counter()
x = do_risset_fast("Tunes/Henry_music_work.txt", tune_length, freqs_per_note, sr)
toc = time.perf_counter()
print(f"Fast risset took {toc - tic:0.4f} seconds")
ipd.Audio(x, rate=sr)

Fast risset took 5.1633 seconds


# Examples
## Slow

In [17]:
# arpeggio - slow algo
tune_length = 2.5
freqs_per_note = 25
sr = 8000
x = do_risset_slow("Tunes/arpeggio.txt", tune_length, freqs_per_note, sr)
ipd.Audio(x, rate=sr)

In [6]:
# birthday - slow algo
tune_length = 10
freqs_per_note = 100
sr = 8000
x = do_risset_slow("Tunes/birthday.txt", tune_length, freqs_per_note, sr)
ipd.Audio(x, rate=sr)

## Fast

In [28]:
# arpeggio - fast algo
tune_length = 2.5
freqs_per_note = 25
sr = 8000
x = do_risset_fast("Tunes/arpeggio.txt", tune_length, freqs_per_note, sr)
ipd.Audio(x, rate=sr)

In [33]:
# wanna - fast algo
tune_length = 70
freqs_per_note = 500
sr = 8000
tic = time.perf_counter()
x = do_risset_fast("Tunes/wanna.txt", tune_length, freqs_per_note, sr)
toc = time.perf_counter()
print(f"Fast risset took {toc - tic:0.4f} seconds")
ipd.Audio(x, rate=sr)

Fast risset took 33.4288 seconds


In [32]:
tune_length = 70
freqs_per_note = 500
sr = 8000
tic = time.perf_counter()
x = do_risset_slow("Tunes/wanna.txt", tune_length, freqs_per_note, sr)
toc = time.perf_counter()
print(f"slow risset took {toc - tic:0.4f} seconds")
ipd.Audio(x, rate=sr)

slow risset took 477.4593 seconds
